In [2]:
# !pip install pyshark

In [3]:
#!zypper in tshark

In [4]:
!tshark -v

TShark (Wireshark) 3.6.2 (Git v3.6.2 packaged as 3.6.2-2)

Copyright 1998-2022 Gerald Combs <gerald@wireshark.org> and contributors.
License GPLv2+: GNU GPL version 2 or later <https://www.gnu.org/licenses/gpl-2.0.html>
This is free software; see the source for copying conditions. There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.

Compiled (64-bit) using GCC 11.2.0, with libpcap, with POSIX capabilities
(Linux), with libnl 3, with GLib 2.71.2, with zlib 1.2.11, with Lua 5.2.4, with
GnuTLS 3.7.3 and PKCS #11 support, with Gcrypt 1.9.4, with MIT Kerberos, with
MaxMind DB resolver, with nghttp2 1.43.0, with brotli, with LZ4, with Zstandard,
with Snappy, with libxml2 2.9.12, with libsmi 0.4.8.

Running on Linux 5.10.16.3-microsoft-standard-WSL2, with Intel(R) Core(TM)
i7-8565U CPU @ 1.80GHz (with SSE4.2), with 25506 MB of physical memory, with
GLib 2.72.4, with zlib 1.2.11, with libpcap 1.10.1 (with TPACKET_V3), with
c-ares 1.18.1, with GnuTLS 3.7.3, w

# Indicate a specific kind of attack

- https://challenge.fra.se/

In [6]:
import pyshark

In [20]:
def capture_packets(capture):
    # Counters for various potential attack indicators
    syn_count = 0
    fin_count = 0
    unique_ips = set()
    print('packing')

    for packet in capture:
        print(type(packet))
        print('XmlLayer' in packet)
        print('TCP' in packet)
        # Check for SYN packets - potential SYN flood (part of DDoS)
        if 'TCP' in packet and packet.tcp.flags_syn == '1':
            syn_count += 1

        # Check for FIN packets - potential FIN scan
        if 'TCP' in packet and packet.tcp.flags_fin == '1':
            fin_count += 1

        # Collect unique source IPs - high count might indicate DDoS
        if 'IP' in packet:
            unique_ips.add(packet.ip.src)

In [17]:
def identify_attack_type(capture):
    # Counters for various potential attack indicators
    syn_count = 0
    fin_count = 0
    unique_ips = set()
    print('packing')

    for packet in capture:
        # Check for SYN packets - potential SYN flood (part of DDoS)
        if 'TCP' in packet and packet.tcp.flags_syn == '1':
            syn_count += 1

        # Check for FIN packets - potential FIN scan
        if 'TCP' in packet and packet.tcp.flags_fin == '1':
            fin_count += 1

        # Collect unique source IPs - high count might indicate DDoS
        if 'IP' in packet:
            unique_ips.add(packet.ip.src)

    # Simple analysis to identify potential attacks
    if syn_count > 1000:  # Threshold value is an example
        print("Potential SYN Flood (DDoS) attack detected.")
    if fin_count > 1000:  # Threshold value is an example
        print("Potential FIN Scan detected.")
    if len(unique_ips) > 100:  # Threshold value is an example
        print("Potential Distributed DoS attack detected due to high number of unique IPs.")

In [ ]:
 with pyshark.FileCapture( <FILE_NAME>.pcap) as filtered_cap:


In [24]:
def print_pkt(pkt):
    print(pkt)

In [10]:
def attack_pcap(file_path):
    cap = pyshark.FileCapture(file_path)

    try:
        # await cap.packets_from_tshark(print_pkt)
        # await cap.packets_from_tshark(identify_attack_type)
        # identify_attack_type(cap)
        cap.packets_from_tshark(capture_packets)
    except Exception as e:
        # This block is executed if there is any exception in the try block
        print(f"An error occurred: {e}")
    finally:
        # This block is executed regardless of what happens in the try and except blocks
        cap.close()


In [4]:
file_path = 'challenges/challenge/challenge.pcap'
file_path = 'challenges/challenge/analytikertestet.pcap'
file_path = 'challenges/challenge/trafik.pcap'

In [26]:
cap = pyshark.FileCapture(file_path)
# cap = pyshark.FileCapture(file_path, include_raw=True, use_json=True)
await cap.packets_from_tshark(capture_packets)
# await cap.packets_from_tshark(print_pkt)

packing
<class 'pyshark.packet.layers.xml_layer.XmlLayer'>


TypeError: argument of type 'XmlLayer' is not iterable

In [13]:
await attack_pcap(file_path)

/tmp/ipykernel_1142/1985430645.py:8: RuntimeWarning: coroutine 'Capture.packets_from_tshark' was never awaited
  cap.packets_from_tshark(capture_packets)
/home/hula/.local/lib/python3.10/site-packages/pygments/regexopt.py:77: RuntimeWarning: coroutine 'Capture.close_async' was never awaited
  '|'.join(regex_opt_inner(list(group[1]), '')


RuntimeError: This event loop is already running

In [ ]:
async def capture_packets():
    # Example: capturing live packets
    # capture = pyshark.LiveCapture(interface=<'your_network_interface')
    capture = pyshark.FileCapture(file_path)
    # await capture.sniff(timeout=50)
    for packet in capture:
        print(packet)

# Run the async function
# await capture = pyshark.FileCapture(file_path)
await capture_packets()

RuntimeError: This event loop is already running

In [34]:
def print_payload(capture):
    for packet in capture:
        field_names = packet.tcp._all_fields
        field_values = packet.tcp._all_fields.values()
        for field_name in field_names:
            for field_value in field_values:
                if field_name == 'tcp.payload':
                    print(f'{field_name} -- {field_value}')

In [36]:
cap = pyshark.FileCapture(file_path, display_filter='tcp')
await cap.packets_from_tshark(print_payload)

AttributeError: No such field tcp

In [ ]:
def capture_packets(capture):
    for packet in capture:
        print(f"Packet: {packet}")


In [ ]:
cap = pyshark.FileCapture(file_path)
await cap.packets_from_tshark(capture_packets)

Packet: Layer ETH
:	Destination: 02:42:ac:17:00:02
	Address: 02:42:ac:17:00:02
	.... ..1. .... .... .... .... = LG bit: Locally administered address (this is NOT the factory default)
	.... ...0 .... .... .... .... = IG bit: Individual address (unicast)
	Source: 02:42:ac:17:00:03
	.... ..1. .... .... .... .... = LG bit: Locally administered address (this is NOT the factory default)
	.... ...0 .... .... .... .... = IG bit: Individual address (unicast)
	Type: IPv4 (0x0800)
	Address: 02:42:ac:17:00:03

Packet: Layer IP
:	0100 .... = Version: 4
	.... 0101 = Header Length: 20 bytes (5)
	Differentiated Services Field: 0x00 (DSCP: CS0, ECN: Not-ECT)
	0000 00.. = Differentiated Services Codepoint: Default (0)
	.... ..00 = Explicit Congestion Notification: Not ECN-Capable Transport (0)
	Total Length: 60
	Identification: 0xc71e (50974)
	Flags: 0x40, Don't fragment
	0... .... = Reserved bit: Not set
	.1.. .... = Don't fragment: Set
	..0. .... = More fragments: Not set
	...0 0000 0000 0000 = Fragme

In [ ]:
# Function to process packets asynchronously
async def process_packets_async(file_path):
    # Create a FileCapture object which is a context manager
    async with pyshark.FileCapture(file_path, use_json=True, include_raw=True, keep_packets=False) as capture:
        async for packet in capture:
            # Process each packet here
            # For example, print out some packet details
            print(f"Packet: {packet}")

# Running the async packet processing function
await process_packets_async(file_path)

TypeError: 'async for' requires an object with __aiter__ method, got FileCapture

In [ ]:
def print_pkt(pkt):
    print(pkt)

pkt = pyshark.FileCapture(file_path)
await pkt.packets_from_tshark(print_pkt)

Packet (Length: 74)
Layer ETH
:	Destination: 02:42:ac:17:00:02
	Address: 02:42:ac:17:00:02
	.... ..1. .... .... .... .... = LG bit: Locally administered address (this is NOT the factory default)
	.... ...0 .... .... .... .... = IG bit: Individual address (unicast)
	Source: 02:42:ac:17:00:03
	.... ..1. .... .... .... .... = LG bit: Locally administered address (this is NOT the factory default)
	.... ...0 .... .... .... .... = IG bit: Individual address (unicast)
	Type: IPv4 (0x0800)
	Address: 02:42:ac:17:00:03
Layer IP
:	0100 .... = Version: 4
	.... 0101 = Header Length: 20 bytes (5)
	Differentiated Services Field: 0x00 (DSCP: CS0, ECN: Not-ECT)
	0000 00.. = Differentiated Services Codepoint: Default (0)
	.... ..00 = Explicit Congestion Notification: Not ECN-Capable Transport (0)
	Total Length: 60
	Identification: 0xc71e (50974)
	Flags: 0x40, Don't fragment
	0... .... = Reserved bit: Not set
	.1.. .... = Don't fragment: Set
	..0. .... = More fragments: Not set
	...0 0000 0000 0000 = Fra